In [1]:
import numpy as np
import os, sys
sys.path.append('../')
from src.datasets.soccernet_generic import soccernet_dataset_generic
from src.utils.helper import samples_by_language
import torch
from torch.utils.data import Dataset, DataLoader

/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torchaudio/backend/utils.py:54: UserWarning: "sox" backend is being deprecated. The default backend will be changed to "sox_io" backend in 0.8.0 and "sox" backend will be removed in 0.9.0. Please migrate to "sox_io" backend. Please refer to https://github.com/pytorch/audio/issues/903 for the detail.
  '"sox" backend is being deprecated. '


In [2]:
root_dir = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/"
train_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Train_300.npy"
valid_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Valid_100.npy"
test_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Test_100.npy"


In [3]:
%%bash
which python3

/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/bin/python3


In [4]:
%%bash
nvidia-smi

Tue Nov 24 02:55:24 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 418.165.02   Driver Version: 418.165.02   CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM3...  On   | 00000000:E2:00.0 Off |                    0 |
| N/A   28C    P0    48W / 350W |      0MiB / 32480MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [5]:
langpath_train = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/train_lang_dict.json'
langpath_valid = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/valid_lang_dict.json'
langpath_test = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/test_lang_dict.json'

samples_train = samples_by_language(langpath_train,train_list,'eng')
samples_valid = samples_by_language(langpath_valid,valid_list,'eng')
samples_test = samples_by_language(langpath_test,test_list,'eng')


In [6]:
train_set = soccernet_dataset_generic(npy_file=train_list,root_dir=root_dir,lang='eng',lang_dict=langpath_train,)
valid_set = soccernet_dataset_generic(npy_file=valid_list,root_dir=root_dir,lang='eng',lang_dict=langpath_valid)


In [14]:
train_set.load_waves()
valid_set.load_waves()
train_set.generate_mel_spectrograms()
valid_set.generate_mel_spectrograms()

NameError: name 'train_set' is not defined

/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torchaudio/functional.py:318: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (128) may be set too high. Or, the value for `n_freqs` (257) may be set too low.
  "At least one mel filterbank has all zero values. "
/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/functional.py:516: UserWarning: stft will require the return_complex parameter be explicitly  specified in a future PyTorch release. Use return_complex=False  to preserve the current behavior or return_complex=True to return  a complex output. (Triggered internally at  /pytorch/aten/src/ATen/native/SpectralOps.cpp:653.)
  normalized, onesided, return_complex)
/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/functional.py:516: UserWarning: The function torch.rfft is deprecated and will be removed i

In [9]:
train_set.load_resnet_features()
valid_set.load_resnet_features()


# Train on resnet features

In [332]:
import torch.nn as nn
import torch.nn.functional as F


class Net(nn.Module):
    def __init__(self,window_size):
        super(Net, self).__init__()
        self.conv1 = nn.Conv2d(in_channels=1, out_channels=128, kernel_size=(512,1))
        self.bn1 = nn.BatchNorm2d(self.conv1.out_channels)
        self.conv2 = nn.Conv2d(self.conv1.out_channels, 16, 1)
        self.bn2 = nn.BatchNorm2d(self.conv2.out_channels)
        self.fc1 = nn.Linear(16*window_size, 120)
        self.fc2 = nn.Linear(self.fc1.out_features, 84)
        self.fc3 = nn.Linear(84, 3)

    def forward(self, x):
        x = F.relu(self.bn1(self.conv1(x)))
        x = F.relu(self.bn2(self.conv2(x)))
        x = x.view(-1,16*window_size)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

In [ ]:
window_sizes = [2,4,8,16,32,64]
train_set = soccernet_dataset_generic(npy_file=train_list,root_dir=root_dir,lang='eng',lang_dict=langpath_train,window_size=w)
valid_set = soccernet_dataset_generic(npy_file=valid_list,root_dir=root_dir,lang='eng',lang_dict=langpath_valid,window_size=w)
train_set.load_waves()
valid_set.load_waves()

accuracies = list()
training_curves = list()
validation curves = list()
for w in window_sizes:    
    # initialize network optimizers etc
    # set windowsize
    train_set.set_window_size(w)
    valid_set.set_window_size(w)
    
    
    #train
    for epoch in range(epochs):
        ...
    #
    accuracies.append()

In [304]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

net = Net()
import torch.optim as optim

criterion = nn.CrossEntropyLoss()

optimizer = optim.SGD(net.parameters(), lr=0.025, momentum=0.9)

In [311]:
# Disable warnings
import warnings
warnings.filterwarnings('ignore')

params = {'batch_size': 12,
         'shuffle': True,
         'num_workers':0,
         'drop_last':True}

In [313]:
validloader = DataLoader(ds,**params)

In [317]:
net.to(device)
epochs = 3
for epoch in range(epochs):
    for i, data in enumerate(validloader,0):
        inputs = data['resnet_spot'].unsqueeze(1).permute(0,1,3,2).to(device)
        target = data['label'].to(device)
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        loss = criterion(outputs, target)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()
        if i % 2000 == 1999:    # print every 2000 mini-batches
            print('[%d, %5d] loss: %.3f' %
                  (epoch + 1, i + 1, running_loss / 2000))
            running_loss = 0.0

            # print statistics
            running_loss += loss.item()
            if i % 5 == 0:    # print every 2000 mini-batches

                writer.add_scalar('training loss',
                                running_loss / 5,
                                epoch * len(validloader) + i)

                print('[%d, %5d] loss: %.3f' %
                      (epoch + 1, i + 1, running_loss / 5))
                running_loss = 0.0

        # calculate accuracy
        with torch.no_grad():
            net.eval()
            res = torch.zeros((3,3))
            for i, data in enumerate(testloader, 0):
                # get the inputs; data is a list of [inputs, labels]
                inputs = data['resnet_spot'].unsqueeze(1).permute(0,1,3,2).to(device)
                label = data['label'].to(device)

                # forward + backward + optimize
                outputs = net(inputs)

                preds = torch.argmax(outputs,dim=1)

                for p,gt in zip(preds,label):
                    res[int(p),int(gt)] += 1




            N_total = res.sum()
            N_correct = res.diag().sum()

            acc = N_correct / N_total

            print(f"Epoch : {epoch}, Accuracy : {acc}")


        print('Finished Training')


2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Siz

torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size(

...

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size(

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Siz

In [310]:
net(inputs)

tensor([[ 0.0086,  0.1328,  0.0407],
        [ 0.0012,  0.1047,  0.0661],
        [ 0.0299,  0.1254,  0.0286],
        [ 0.0426,  0.1046, -0.0681],
        [-0.0111,  0.1068,  0.0298],
        [-0.0160,  0.0872, -0.0040],
        [-0.0516,  0.1086, -0.0444],
        [ 0.0011,  0.1241,  0.0715],
        [ 0.0485,  0.0594,  0.0318],
        [-0.0433,  0.1395,  0.0982],
        [-0.0032,  0.0727,  0.0642],
        [-0.0388,  0.1168,  0.0688]], device='cuda:0', grad_fn=<AddmmBackward>)

# Train on audio

In [330]:
import torchvision
densenet = torchvision.models.densenet161(pretrained=True)
densenet.features.conv0 = nn.Conv2d(1, 96, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
densenet.classifier = nn.Linear(in_features=densenet.classifier.in_features, out_features=3,bias=True)
import torch.optim as optim

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(densenet.parameters(), lr=0.001, momentum=0.9)


In [331]:
densenet.to(device)
epochs = 3
for epoch in range(epochs):
    for i, data in enumerate(validloader,0):
        inputs = data['ms_spot'].unsqueeze(1).permute(0,1,3,2).to(device)
        print(inputs.size())
        target = data['label'].to(device)
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = densenet(inputs)
        loss = criterion(outputs, target)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()
        if i % 2000 == 1999:    # print every 2000 mini-batches
            print('[%d, %5d] loss: %.3f' %
                  (epoch + 1, i + 1, running_loss / 2000))
            running_loss = 0.0

            # print statistics
            running_loss += loss.item()
            if i % 5 == 0:    # print every 2000 mini-batches

                writer.add_scalar('training loss',
                                running_loss / 5,
                                epoch * len(validloader) + i)

                print('[%d, %5d] loss: %.3f' %
                      (epoch + 1, i + 1, running_loss / 5))
                running_loss = 0.0

        # calculate accuracy
        with torch.no_grad():
            net.eval()
            res = torch.zeros((3,3))
            for i, data in enumerate(testloader, 0):
                # get the inputs; data is a list of [inputs, labels]
                inputs = data['ms_spot'].unsqueeze(1).permute(0,1,3,2).to(device)
                label = data['label'].to(device)

                # forward + backward + optimize
                outputs = densenet(inputs)

                preds = torch.argmax(outputs,dim=1)

                for p,gt in zip(preds,label):
                    res[int(p),int(gt)] += 1




            N_total = res.sum()
            N_correct = res.diag().sum()

            acc = N_correct / N_total

            print(f"Epoch : {epoch}, Accuracy : {acc}")


        print('Finished Training')


2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
torch.Size([12, 1, 160, 127])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
to

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

...

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Siz

1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
Epoch : 2, Accuracy : 0.3123486638069153
Finished Training
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 16

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
1
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Size([8, 512])
2
torch.Size([127, 160])
torch.Siz

# Merge models 1 - softmax average during eval

# Merge models 2 - layers and training